In [44]:
#importaciones
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import matplotlib.pyplot as plt

#importaciones locales
import re
import ipywidgets as widgets
from IPython.display import display


In [45]:
#Leer las bases de datos
movies=pd.read_csv("movies.csv")
with pd.option_context('display.max_rows',None):
    print(movies)



       movieId                                              title  \
0            1                                   Toy Story (1995)   
1            2                                     Jumanji (1995)   
2            3                            Grumpier Old Men (1995)   
3            4                           Waiting to Exhale (1995)   
4            5                 Father of the Bride Part II (1995)   
5            6                                        Heat (1995)   
6            7                                     Sabrina (1995)   
7            8                                Tom and Huck (1995)   
8            9                                Sudden Death (1995)   
9           10                                   GoldenEye (1995)   
10          11                     American President, The (1995)   
11          12                 Dracula: Dead and Loving It (1995)   
12          13                                       Balto (1995)   
13          14                    

In [46]:
#Limpiemos los títulos para eliminar los caracteres especiales a través de una función

def clean_title(title):
    return re.sub("[^a-zA-Z0-9 ]","",title)

#creamos una nueva columna en el dataframe que ya tenemos llamado movies, con la columna limpia
movies["clean_title"]=movies["title"].apply(clean_title)
movies

movieId                               title  \
0            1                    Toy Story (1995)   
1            2                      Jumanji (1995)   
2            3             Grumpier Old Men (1995)   
3            4            Waiting to Exhale (1995)   
4            5  Father of the Bride Part II (1995)   
...        ...                                 ...   
62418   209157                           We (2018)   
62419   209159           Window of the Soul (2001)   
62420   209163                    Bad Poems (2018)   
62421   209169                 A Girl Thing (2001)   
62422   209171      Women of Devil's Island (1962)   

                                            genres  \
0      Adventure|Animation|Children|Comedy|Fantasy   
1                       Adventure|Children|Fantasy   
2                                   Comedy|Romance   
3                             Comedy|Drama|Romance   
4                                           Comedy   
...                                            ...   
62418                                        Drama   
62419                                  Documentary   
62420                                 Comedy|Drama   
62421                           (no genres listed)   
62422                       Action|Adventure|Drama   

                            clean_title  
0                        Toy Story 1995  
1                          Jumanji 1995  
2                 Grumpier Old Men 1995  
3                Waiting to Exhale 1995  
4      Father of the Bride Part II 1995  
...                                 ...  
62418                           We 2018  
62419           Window of the Soul 2001  
62420                    Bad Poems 2018  
62421                 A Girl Thing 2001  
62422       Women of Devils Island 1962  

[62423 rows x 4 columns]

In [47]:
#Se crea un buscador. Necesitamos la frecuencia en la que aparecen las palabras en un título. 
#Si las palabras son muy comunes, se eliminan.
#La "inverse document frequency" determina con qué frecuencia aparece una palabra. se penaliza a las palabras con mayor frecuencia

#se inicializa la clase creando un objeto de tipo TfidVectorizer
vectorizador=TfidfVectorizer(ngram_range=(1,2)) #ngram_range determina que deben considerarse pares de palabras "toy story", "story 1995"
type(vectorizador)

sklearn.feature_extraction.text.TfidfVectorizer

In [48]:
tfidf=vectorizador.fit_transform(movies["clean_title"])

In [49]:
#Calcular que tan similar es un elemento a nuestra transformación
#Calcula un número que indica que tan parecido es el título a los datos de la columna de titulos limpiada

def search(title):
    title=clean_title(title)
    query_vec=vectorizador.transform([title])
    similarity=cosine_similarity(query_vec,tfidf).flatten()

    #Se busca cuales titulos tienen la mayor similaridad
    #Argpartition busca las ubicaciones donde el valor el menor, al pasar -10, busca los 10 mayores valores, y luego se ordenan
    #desde el mayor (último) hasta el menor (primero) en la lista de 10
    indices=np.argpartition(similarity,-10)[-10:]

    #extraer los títulos que nos interesan, usando como índices los indices calculados
    results=movies.iloc[indices][::-1] #Se invierten de forma que el más similar quede arriba
    return results

In [72]:
search("dark knight")

movieId                          title                       genres  \
12221    58559        Dark Knight, The (2008)      Action|Crime|Drama|IMAX   
27811   130219         The Dark Knight (2011)  Action|Crime|Drama|Thriller   
4793      4899            Black Knight (2001)     Adventure|Comedy|Fantasy   
17464    91529  Dark Knight Rises, The (2012)  Action|Adventure|Crime|IMAX   
166        168            First Knight (1995)         Action|Drama|Romance   
46381   172327            Knight Rider (2008)           (no genres listed)   
28055   130820           Street Knight (1993)           (no genres listed)   
33974   144392       Underdog Knight 2 (2011)                       Action   
6881      7006            Knight Moves (1992)             Mystery|Thriller   
26083   125147        The Black Knight (1954)             Action|Adventure   

                      clean_title  
12221        Dark Knight The 2008  
27811        The Dark Knight 2011  
4793            Black Knight 2001  
17464  Dark Knight Rises The 2012  
166             First Knight 1995  
46381           Knight Rider 2008  
28055          Street Knight 1993  
33974      Underdog Knight 2 2011  
6881            Knight Moves 1992  
26083       The Black Knight 1954

In [51]:
#Se crea un widget para buscar automáticamente
#El widget no funciona. Haré el código en texto

# movie_input=widgets.Text(value="Toy Story",description="Título de la película:",disabled=False)
# movie_list=widgets.Output()

# def on_type(data):
#     with movie_list:
#         movie_list.clear_output()
#         title=data["new"]
#         if len(title)>5:
#             display(search(title))
            
# movie_input.observe(on_type,names="value")
# display(movie_input,movie_list)

In [52]:
# #Se busca automáticamente para una entrada del usuario
# movie_input=input()

# def on_type(data):
#     return search(data)
            
# peliculas=on_type(movie_input)
# peliculas

In [53]:

#Segunda parte. Considerar los ratings de los usuarios de las películas para hacer recomendaciones

ratings=pd.read_csv('ratings.csv')
ratings

userId  movieId  rating   timestamp
0              1      296     5.0  1147880044
1              1      306     3.5  1147868817
2              1      307     5.0  1147868828
3              1      665     5.0  1147878820
4              1      899     3.5  1147868510
...          ...      ...     ...         ...
25000090  162541    50872     4.5  1240953372
25000091  162541    55768     2.5  1240951998
25000092  162541    56176     2.0  1240950697
25000093  162541    58559     4.0  1240953434
25000094  162541    63876     5.0  1240952515

[25000095 rows x 4 columns]

In [54]:
#buscar las películas que son parecidas a la que pongo
movie_id=1
#Se desea buscar en ratings cuales películas tienen el mismo id que el mio, y además cuales tienen a la vez un rating mayor que 4
similar_users=ratings[ (ratings["movieId"]==movie_id) &  (ratings["rating"]>4) ]["userId"].unique()
len(similar_users)

18835

In [55]:
similar_users

array([    36,     75,     86, ..., 162527, 162530, 162533], dtype=int64)

In [56]:
#ahora reviso ratings de manera que los usuarios que tengan el mismo código que los similares y además tengan un rating mayor que cuatro
#sean reportados, y veo el id de la película
similar_user_recs=ratings[(ratings["userId"].isin(similar_users))&(ratings["rating"]>4)]["movieId"]

In [57]:
similar_user_recs

5101            1
5105           34
5111          110
5114          150
5127          260
            ...  
24998854    60069
24998861    67997
24998876    78499
24998884    81591
24998888    88129
Name: movieId, Length: 1358326, dtype: int64

In [58]:
#Pero todos los usuarios son muchos. Quiero ver aquellos que están en el 10% de los favoritos
similar_user_recs=similar_user_recs.value_counts()/len(similar_users)
similar_user_recs=similar_user_recs[similar_user_recs>0.1]
similar_user_recs

1        1.000000
318      0.445607
260      0.403770
356      0.370215
296      0.367295
           ...   
953      0.103053
551      0.101195
1222     0.100876
745      0.100345
48780    0.100186
Name: movieId, Length: 113, dtype: float64

In [59]:
#Hay que buscar películas parecidas, no las que son populares nada más. La solución que se tiene ahora incluye las comunes y gustadas por todos
#Pero hay que buscar solo las que son parecidas

#Se estudia cuales de todos los usuarios son parecidos
all_users =ratings[ ( ratings["movieId"].isin(similar_user_recs.index) ) & ( ratings["rating"]>4 ) ]
#ahora se determina de estos usuarios, cuales son los porcentajes de parecido
all_users_recs = all_users["movieId"].value_counts()/len(all_users["userId"].unique())
all_users_recs

318      0.342220
296      0.284674
2571     0.244033
356      0.235266
593      0.225909
           ...   
551      0.040918
50872    0.039111
745      0.037031
78499    0.035131
2355     0.025091
Name: movieId, Length: 113, dtype: float64

In [60]:
#Comparar los porcentajes, combinando las series juntas
rec_percentages=pd.concat([similar_user_recs,all_users_recs],axis=1)
rec_percentages.columns=['similar','all']

In [61]:
rec_percentages

similar       all
1      1.000000  0.124728
318    0.445607  0.342220
260    0.403770  0.222207
356    0.370215  0.235266
296    0.367295  0.284674
...         ...       ...
953    0.103053  0.045792
551    0.101195  0.040918
1222   0.100876  0.066877
745    0.100345  0.037031
48780  0.100186  0.068314

[113 rows x 2 columns]

In [62]:
#Se desea que el porcentaje similar sea lo más diferente posible al total. de esta forma se tiene que
rec_percentages['score']=rec_percentages['similar']/rec_percentages['all']
#se ordena el dataframe
rec_percentages=rec_percentages.sort_values("score",ascending=False)
rec_percentages

similar       all     score
1      1.000000  0.124728  8.017414
3114   0.280648  0.053706  5.225654
2355   0.110539  0.025091  4.405452
78499  0.152960  0.035131  4.354038
4886   0.235147  0.070811  3.320783
...         ...       ...       ...
2858   0.216724  0.167634  1.292845
296    0.367295  0.284674  1.290232
79132  0.166817  0.131384  1.269693
4973   0.142501  0.112405  1.267747
2959   0.262649  0.216717  1.211946

[113 rows x 3 columns]

In [63]:
#Se toman las primeras 10 y se combinan con los ids de las películas
rec_percentages.head(10).merge(movies, left_index=True,right_on="movieId")

similar       all     score  movieId                        title  \
0      1.000000  0.124728  8.017414        1             Toy Story (1995)   
3021   0.280648  0.053706  5.225654     3114           Toy Story 2 (1999)   
2264   0.110539  0.025091  4.405452     2355         Bug's Life, A (1998)   
14813  0.152960  0.035131  4.354038    78499           Toy Story 3 (2010)   
4780   0.235147  0.070811  3.320783     4886        Monsters, Inc. (2001)   
580    0.216618  0.067513  3.208539      588               Aladdin (1992)   
6258   0.228139  0.072268  3.156862     6377          Finding Nemo (2003)   
587    0.179400  0.059977  2.991150      595  Beauty and the Beast (1991)   
8246   0.203504  0.068453  2.972889     8961      Incredibles, The (2004)   
359    0.253411  0.085764  2.954762      364        Lion King, The (1994)   

                                                 genres  \
0           Adventure|Animation|Children|Comedy|Fantasy   
3021        Adventure|Animation|Children|Comedy|Fantasy   
2264                Adventure|Animation|Children|Comedy   
14813  Adventure|Animation|Children|Comedy|Fantasy|IMAX   
4780        Adventure|Animation|Children|Comedy|Fantasy   
580         Adventure|Animation|Children|Comedy|Musical   
6258                Adventure|Animation|Children|Comedy   
587     Animation|Children|Fantasy|Musical|Romance|IMAX   
8246         Action|Adventure|Animation|Children|Comedy   
359     Adventure|Animation|Children|Drama|Musical|IMAX   

                     clean_title  
0                 Toy Story 1995  
3021            Toy Story 2 1999  
2264            Bugs Life A 1998  
14813           Toy Story 3 2010  
4780           Monsters Inc 2001  
580                 Aladdin 1992  
6258           Finding Nemo 2003  
587    Beauty and the Beast 1991  
8246        Incredibles The 2004  
359           Lion King The 1994

In [67]:
#Ahora se combina en una función que haga la recomendación
def find_similar_movies(movie_id,x,pc):
    #x es el rating
    #pc es el porcentaje de valores deseados
    #Se importan los datos
    movies=pd.read_csv("movies.csv")
    ratings=pd.read_csv('ratings.csv')
    #Se desea buscar en ratings cuales películas tienen el mismo id que el mio, y además cuales tienen a la vez un rating mayor que x
    similar_users=ratings[ (ratings["movieId"]==movie_id) &  (ratings["rating"]>x) ]["userId"].unique()
    #ahora reviso ratings de manera que los usuarios que tengan el mismo código que los similares y además tengan un rating mayor que x
    #sean reportados, y veo el id de la película
    similar_user_recs=ratings[(ratings["userId"].isin(similar_users))&(ratings["rating"]>4)]["movieId"]
    #Pero todos los usuarios son muchos. Quiero ver aquellos que están en el pc% de los favoritos
    similar_user_recs=similar_user_recs.value_counts()/len(similar_users)
    similar_user_recs=similar_user_recs[similar_user_recs>pc]
    #Se estudia cuales de todos los usuarios son parecidos
    all_users =ratings[ ( ratings["movieId"].isin(similar_user_recs.index) ) & ( ratings["rating"]>x ) ]
    #ahora se determina de estos usuarios, cuales son los porcentajes de parecido
    all_users_recs = all_users["movieId"].value_counts()/len(all_users["userId"].unique())
    #Comparar los porcentajes, combinando las series juntas
    rec_percentages=pd.concat([similar_user_recs,all_users_recs],axis=1)
    rec_percentages.columns=['similar','all']
    #Se desea que el porcentaje similar sea lo más diferente posible al total. de esta forma se tiene que
    rec_percentages['score']=rec_percentages['similar']/rec_percentages['all']
    #se ordena el dataframe
    rec_percentages=rec_percentages.sort_values("score",ascending=False)
    return rec_percentages.head(10).merge(movies, left_index=True,right_on="movieId")[["movieId","score","title","genres"]]

In [74]:
find_similar_movies(58559,3,0.2)

movieId     score                                              title  \
12221    58559  2.522808                            Dark Knight, The (2008)   
17464    91529  1.889443                      Dark Knight Rises, The (2012)   
14937    79132  1.702856                                   Inception (2010)   
21199   109487  1.686148                                Interstellar (2014)   
13249    68157  1.596698                        Inglourious Basterds (2009)   
11163    48780  1.573785                               Prestige, The (2006)   
11124    48516  1.513172                               Departed, The (2006)   
12429    60069  1.414484                                      WALL·E (2008)   
10002    33794  1.336003                               Batman Begins (2005)   
7028      7153  1.309087  Lord of the Rings: The Return of the King, The...   

                                                genres  
12221                          Action|Crime|Drama|IMAX  
17464                      Action|Adventure|Crime|IMAX  
14937  Action|Crime|Drama|Mystery|Sci-Fi|Thriller|IMAX  
21199                                      Sci-Fi|IMAX  
13249                                 Action|Drama|War  
11163                    Drama|Mystery|Sci-Fi|Thriller  
11124                             Crime|Drama|Thriller  
12429      Adventure|Animation|Children|Romance|Sci-Fi  
10002                                Action|Crime|IMAX  
7028                    Action|Adventure|Drama|Fantasy